In [2]:
library(tidyverse)

── Attaching packages ─────────────────────────────────────── tidyverse 1.3.2 ──
✔ ggplot2 3.3.6      ✔ purrr   0.3.4 
✔ tibble  3.1.8      ✔ dplyr   1.0.10
✔ tidyr   1.2.1      ✔ stringr 1.4.1 
✔ readr   2.1.2      ✔ forcats 0.5.2 
── Conflicts ────────────────────────────────────────── tidyverse_conflicts() ──
✖ dplyr::filter() masks stats::filter()
✖ dplyr::lag()    masks stats::lag()


In [35]:
ME  = qs::qread('_targets/objects/ME_MOL')
ME %>% head

MOL_M00     MOL_M01      MOL_M02      MOL_M03    
ATTACTCTCCGCGGAT_1_1 -0.03744332  0.001868734  0.092854480 -0.01481858
AGTTCGAAGAAACCAT_1_1 -0.03168586  0.009315183  0.091708728 -0.01045180
CACGGGTGTTACACTG_1_1 -0.01191233  0.054573955  0.001239567  0.04608620
GCCAACGGTTGTTTGG_1_1 -0.01361687  0.074002171 -0.016341037 -0.01021857
CGAAGGAAGCACGATG_1_1 -0.05213193 -0.022287682  0.091092923 -0.01854006
GTAACACCATATGGCT_1_1  0.01298801  0.022775556  0.013993283  0.01684595
                     MOL_M04      MOL_M05      MOL_M06      orig.ident
ATTACTCTCCGCGGAT_1_1 -0.007153317 -0.057370402 -0.073784285 SI-TT-A11 
AGTTCGAAGAAACCAT_1_1 -0.022617640 -0.057370776 -0.070825816 SI-TT-A11 
CACGGGTGTTACACTG_1_1 -0.028513546 -0.058321399 -0.014924954 SI-TT-A11 
GCCAACGGTTGTTTGG_1_1 -0.033064961 -0.042299581 -0.022234310 SI-TT-A11 
CGAAGGAAGCACGATG_1_1 -0.021284472 -0.108746447 -0.072847848 SI-TT-A11 
GTAACACCATATGGCT_1_1 -0.020689493 -0.004796459  0.002338066 SI-TT-A11 
                     nCount_RNA nFeature_RNA ⋯ strain treatment time 
ATTACTCTCCGCGGAT_1_1 22867      4243         ⋯ obob   FGF1      Day14
AGTTCGAAGAAACCAT_1_1 21398      4206         ⋯ BL6    Veh_PF    Day5 
CACGGGTGTTACACTG_1_1 20683      4692         ⋯ obob   FGF1      Day14
GCCAACGGTTGTTTGG_1_1 16528      4347         ⋯ obob   Veh_PF    Day5 
CGAAGGAAGCACGATG_1_1 13777      3094         ⋯ obob   Veh_PF    Day14
GTAACACCATATGGCT_1_1 11782      3149         ⋯ BL6    Veh_PF    Day5 
                     collection_date isolation_date batch    predicted.id
ATTACTCTCCGCGGAT_1_1 220131          22/6/2022      Batch__1 MOL         
AGTTCGAAGAAACCAT_1_1 220329          22/6/2022      Batch__1 MOL         
CACGGGTGTTACACTG_1_1 220131          22/6/2022      Batch__1 MOL         
GCCAACGGTTGTTTGG_1_1 211214          22/6/2022      Batch__1 MOL         
CGAAGGAAGCACGATG_1_1 220407          22/6/2022      Batch__1 MOL         
GTAACACCATATGGCT_1_1 220329          22/6/2022      Batch__1 MOL         
                     prediction.score.max labels group            
ATTACTCTCCGCGGAT_1_1 1.0000000            MOL    FGF1.Day14.obob  
AGTTCGAAGAAACCAT_1_1 1.0000000            MOL    Veh_PF.Day5.BL6  
CACGGGTGTTACACTG_1_1 0.9872625            MOL    FGF1.Day14.obob  
GCCAACGGTTGTTTGG_1_1 0.4832757            MOL    Veh_PF.Day5.obob 
CGAAGGAAGCACGATG_1_1 1.0000000            MOL    Veh_PF.Day14.obob
GTAACACCATATGGCT_1_1 0.9776664            MOL    Veh_PF.Day5.BL6

In [36]:
get_module_cols = function(ME){
    module_cols = ME %>%
    colnames %>%
    stringr::str_subset('_M\\d{2}') %>%
    stringr::str_subset('_M00', negate = TRUE)
    module_cols
}


make_contrasts_fgf1 = function(design){
    contrasts= tribble(
            ~"name", ~"expression",        
            "Day5.obob.FGF1vsVehPF", "FGF1.Day5.obob - Veh_PF.Day5.obob",
            "Day14.obob.FGF1vsVehPF", "FGF1.Day14.obob - Veh_PF.Day14.obob",
            "Day514.obob.FGF1vsVehPF", "(FGF1.Day5.obob + FGF1.Day14.obob)/2 - (Veh_PF.Day5.obob+Veh_PF.Day14.obob)/2",
            "Day5vsDay14.BL6.VehPF", "Veh_PF.Day5.BL6 - Veh_PF.Day14.BL6",
            "Day5vsDay14.obob.VehPF", "Veh_PF.Day5.obob - Veh_PF.Day14.obob") %>%
        deframe
    cm = limma::makeContrasts(
        contrasts=contrasts,
        levels=design
    )
    colnames(cm) = names(contrasts)
    cm
}


fit_limma_me = function(ME, cm, design){
    module_cols = get_module_cols(ME)
    eset = ME[module_cols] %>% t
    group = ME$group
    batch = ME$batch
    design = model.matrix(~0+group+batch)
    colnames(design) = colnames(design) %>%
        str_replace('group', '') %>%
        str_replace('batch', '')
    corfit <- limma::duplicateCorrelation(eset,design,block=ME$hash.mcl.ID)
    fit <- limma::lmFit(eset,design,block=ME$hash.mcl.ID,correlation=corfit$consensus)
    cm = make_contrasts_fgf1(design)
    fit2 <- limma::contrasts.fit(fit, cm)
    fit2 <- limma::eBayes(fit2)
    fit2
}


.get_sig_mod_single = function(fit2, coef){
    limma::topTable(fit2, coef = coef) %>%
    mutate(significant = case_when(adj.P.Val < 0.05 ~ TRUE,
                                   adj.P.Val >= 0.05 ~ FALSE)) %>%
    mutate(comparison = coef) %>%
    rownames_to_column(var = 'module') %>%
    relocate(comparison, module)
}


get_sig_mods = function(fit2){
    top_table = colnames(fit2$contrasts) %>% 
        purrr::map(\(x) .get_sig_mod_single(fit2, x)) %>% 
        do.call(rbind, .)
    top_table
}

In [37]:
targets::tar_meta(fields = error, complete_only = TRUE) %>% filter(str_detect(name, 'modules_wgcna_Agrp'))

name error

In [46]:
top_table = qs::qread('_targets/objects/top_table_Agrp')
top_table

comparison              module   logFC         AveExpr       t           
1  Day5.obob.FGF1vsVehPF   Agrp_M01 -6.819542e-03 -6.913734e-19 -5.604377746
2  Day5.obob.FGF1vsVehPF   Agrp_M02  3.878967e-03  1.393582e-20  3.343331389
3  Day5.obob.FGF1vsVehPF   Agrp_M04  4.824412e-03  3.474001e-19  3.094668833
4  Day5.obob.FGF1vsVehPF   Agrp_M03 -4.076366e-03 -1.025570e-18 -2.576903089
5  Day5.obob.FGF1vsVehPF   Agrp_M08  2.907060e-03  6.856726e-19  2.125483962
6  Day5.obob.FGF1vsVehPF   Agrp_M09  1.684062e-03  1.700502e-20  1.961007761
7  Day5.obob.FGF1vsVehPF   Agrp_M06 -2.261151e-03  8.821871e-19 -1.429773287
8  Day5.obob.FGF1vsVehPF   Agrp_M10  2.273738e-03  5.468522e-19  1.363826499
9  Day5.obob.FGF1vsVehPF   Agrp_M05  1.232472e-03  6.786733e-19  0.750027780
10 Day5.obob.FGF1vsVehPF   Agrp_M07 -9.310805e-04 -8.495415e-19 -0.560608277
11 Day14.obob.FGF1vsVehPF  Agrp_M03 -1.492170e-03 -1.025570e-18 -0.934971021
12 Day14.obob.FGF1vsVehPF  Agrp_M01  9.602914e-04 -6.913734e-19  0.782222373
13 Day14.obob.FGF1vsVehPF  Agrp_M09  6.717778e-04  1.700502e-20  0.775357375
14 Day14.obob.FGF1vsVehPF  Agrp_M07  1.180381e-03 -8.495415e-19  0.704448789
15 Day14.obob.FGF1vsVehPF  Agrp_M06  1.066657e-03  8.821871e-19  0.668524491
16 Day14.obob.FGF1vsVehPF  Agrp_M05  8.194773e-04  6.786733e-19  0.494301788
17 Day14.obob.FGF1vsVehPF  Agrp_M02 -4.716651e-04  1.393582e-20 -0.402950881
18 Day14.obob.FGF1vsVehPF  Agrp_M10 -5.888227e-04  5.468522e-19 -0.350072672
19 Day14.obob.FGF1vsVehPF  Agrp_M08  2.593680e-04  6.856726e-19  0.187964217
20 Day14.obob.FGF1vsVehPF  Agrp_M04  2.633258e-04  3.474001e-19  0.167424198
21 Day514.obob.FGF1vsVehPF Agrp_M01 -2.929625e-03 -6.913734e-19 -3.389562548
22 Day514.obob.FGF1vsVehPF Agrp_M03 -2.784268e-03 -1.025570e-18 -2.477965806
23 Day514.obob.FGF1vsVehPF Agrp_M04  2.543869e-03  3.474001e-19  2.297332726
24 Day514.obob.FGF1vsVehPF Agrp_M02  1.703651e-03  1.393582e-20  2.067299218
25 Day514.obob.FGF1vsVehPF Agrp_M09  1.177920e-03  1.700502e-20  1.931062730
26 Day514.obob.FGF1vsVehPF Agrp_M08  1.583214e-03  6.856726e-19  1.629681869
27 Day514.obob.FGF1vsVehPF Agrp_M05  1.025975e-03  6.786733e-19  0.879014984
28 Day514.obob.FGF1vsVehPF Agrp_M10  8.424578e-04  5.468522e-19  0.711420186
29 Day514.obob.FGF1vsVehPF Agrp_M06 -5.972472e-04  8.821871e-19 -0.531680898
30 Day514.obob.FGF1vsVehPF Agrp_M07  1.246501e-04 -8.495415e-19  0.105663369
31 Day5vsDay14.BL6.VehPF   Agrp_M02 -4.864199e-03  1.393582e-20 -3.138537993
32 Day5vsDay14.BL6.VehPF   Agrp_M09  1.843543e-03  1.700502e-20  1.607041637
33 Day5vsDay14.BL6.VehPF   Agrp_M04 -3.221781e-03  3.474001e-19 -1.547100674
34 Day5vsDay14.BL6.VehPF   Agrp_M01  2.137008e-03 -6.913734e-19  1.314713245
35 Day5vsDay14.BL6.VehPF   Agrp_M03 -1.659636e-03 -1.025570e-18 -0.785398961
36 Day5vsDay14.BL6.VehPF   Agrp_M10 -1.603745e-03  5.468522e-19 -0.720122868
37 Day5vsDay14.BL6.VehPF   Agrp_M05 -1.275168e-03  6.786733e-19 -0.580925201
38 Day5vsDay14.BL6.VehPF   Agrp_M08 -6.523574e-04  6.856726e-19 -0.357060763
39 Day5vsDay14.BL6.VehPF   Agrp_M06 -4.641980e-04  8.821871e-19 -0.219732133
40 Day5vsDay14.BL6.VehPF   Agrp_M07 -1.531675e-05 -8.495415e-19 -0.006903855
41 Day5vsDay14.obob.VehPF  Agrp_M01  6.863334e-03 -6.913734e-19  5.604112652
42 Day5vsDay14.obob.VehPF  Agrp_M02 -4.068738e-03  1.393582e-20 -3.484356243
43 Day5vsDay14.obob.VehPF  Agrp_M06  3.790688e-03  8.821871e-19  2.381525232
44 Day5vsDay14.obob.VehPF  Agrp_M08 -2.716786e-03  6.856726e-19 -1.973598063
45 Day5vsDay14.obob.VehPF  Agrp_M10 -3.043595e-03  5.468522e-19 -1.813865150
46 Day5vsDay14.obob.VehPF  Agrp_M04 -1.990314e-03  3.474001e-19 -1.268501159
47 Day5vsDay14.obob.VehPF  Agrp_M03  1.371926e-03 -1.025570e-18  0.861697799
48 Day5vsDay14.obob.VehPF  Agrp_M09 -5.274333e-04  1.700502e-20 -0.610222665
49 Day5vsDay14.obob.VehPF  Agrp_M07 -7.585960e-04 -8.495415e-19 -0.453818671
50 Day5vsDay14.obob.VehPF  Agrp_M05  4.250673e-04  6.786733e-19  0.257014406
   P.Value      adj.P.Val    B         significant
1  2.208316e-08 2.208316e

In [92]:
gost_results = qs::qread('_targets/objects/gost_result_Agrp')
hubgenes = qs::qread('_targets/objects/hubgenes_Agrp')
gost_results$result

query    significant p_value       term_size query_size intersection_size
1    Agrp_M01 TRUE        1.175070e-119  5555     2340        950             
2    Agrp_M01 TRUE        2.024457e-116  6554     2340       1050             
3    Agrp_M01 TRUE        1.292918e-110  3819     2340        732             
4    Agrp_M01 TRUE        3.543409e-110  3629     2340        708             
5    Agrp_M01 TRUE        6.313176e-101  6007     2340        958             
6    Agrp_M01 TRUE         3.868500e-99  5829     2340        935             
7    Agrp_M01 TRUE         8.692720e-99 14096     2340       1693             
8    Agrp_M01 TRUE         1.670515e-93  5698     2340        908             
9    Agrp_M01 TRUE         2.895597e-91 12348     2340       1531             
10   Agrp_M01 TRUE         2.501321e-89 13379     2340       1612             
11   Agrp_M01 TRUE         1.965424e-87  7368     2340       1065             
12   Agrp_M01 TRUE         2.496583e-87  6862     2340       1014             
13   Agrp_M01 TRUE         4.973924e-85  3423     2340        632             
14   Agrp_M01 TRUE         5.806646e-78 20933     2340       2132             
15   Agrp_M01 TRUE         1.701176e-77  3020     2340        567             
16   Agrp_M01 TRUE         5.708402e-76  3162     2340        581             
17   Agrp_M01 TRUE         1.441435e-74  6714     2340        966             
18   Agrp_M01 TRUE         2.003875e-73  5016     2340        786             
19   Agrp_M01 TRUE         7.975607e-72  5438     2340        827             
20   Agrp_M01 TRUE         3.322800e-71  6028     2340        887             
21   Agrp_M01 TRUE         2.635653e-70  2547     2340        493             
22   Agrp_M01 TRUE         2.666546e-69  2540     2340        490             
23   Agrp_M01 TRUE         6.043242e-66   973     2340        266             
24   Agrp_M01 TRUE         7.843700e-66  4134     2340        670             
25   Agrp_M01 TRUE         3.491758e-65  3232     2340        565             
26   Agrp_M01 TRUE         9.802719e-65 13177     2340       1528             
27   Agrp_M01 TRUE         4.086808e-64  6042     2340        869             
28   Agrp_M01 TRUE         9.105118e-64  1373     2340        323             
29   Agrp_M01 TRUE         2.438299e-63  1533     2340        345             
30   Agrp_M01 TRUE         3.628190e-62  3657     2340        607             
⋮    ⋮        ⋮           ⋮             ⋮         ⋮          ⋮                
3370 Agrp_M09 TRUE        0.0332507035  13535     55         48               
3371 Agrp_M10 TRUE        0.0001632203   2508     48         18               
3372 Agrp_M10 TRUE        0.0038018002    219     48          6               
3373 Agrp_M10 TRUE        0.0076015096    247     48          6               
3374 Agrp_M10 TRUE        0.0132568929   1245     48         11               
3375 Agrp_M10 TRUE        0.0196901737   1844     48         13               
3376 Agrp_M10 TRUE        0.0209640747     81     48          4               
3377 Agrp_M10 TRUE        0.0257642247   1605     48         12               
3378 Agrp_M10 TRUE        0.0261724864   1088     48         10               
3379 Agrp_M10 TRUE        0.0341078745    484     48          7               
3380 Agrp_M10 TRUE        0.0351675487   4003     48         19               
3381 Agrp_M10 TRUE        0.0001084098   1086     50         12               
3382 Agrp_M10 TRUE        0.0005905414    481     50          8               
3383 Agrp_M10 TRUE        0.0011867175   6980     50         28               
3384 Agrp_M10 TRUE        0.0014261236    725     50          9               
3385 Agrp_M10 TRUE        0.0018554345   2558     50         16               
3386 Agrp_M10 TRUE        0.0025881220    781     50          9               
3387 Agrp_M10 TRUE        0.0026413996    783     50          9               
3388 Agrp_M10 TRUE        0.0034580185    810     50   

In [69]:
gost_results$result %>% pull(gene_ids) %>% head

[1] "Eif5b,Pdcl3,Nck2,Tpp2,Bzw1,Cflar,Bmpr2,Abi2,Creb1,Dnajb2,Cab39,Psmd1,Gigyf2,Atg16l1,Ube2f,Asb1,Ccnt2,Rab3gap1,Ubxn4,Elk4,Klhl12,Kdm5b,Tpr,Ivns1abp,Edem3,Abl2,Cop1,Dcaf8,Fmn2,Desi2,Cdc42bpa,Sde2,Dusp10,Rab3gap2,Eprs,Arfgef1,Ube2w,Zfp451,Uggt1,Kansl3,Rnf149,Clk1,Trak2,Als2,Sumo1,Bard1,Marchf4,Usp37,Rnf25,Ptprn,Cul3,Trip12,Col6a3,Hdac4,Pam,Ralb,Ptpn4,Mapkapk2,Btg2,Cdc73,Rnf2,Dhx9,Rasal2,Pappa2,Tiprl,Dcaf6,Uhmk1,Hnrnpu,Wdr26,Fbxo28,Mark1,Tgfb2,Ppp2r5a,Hhat,Stam,Yme1l1,Med27,Sh2d3c,Mapkap1,Epc2,Marchf7,Tank,Psmd14,Ppig,Ubr3,Myo3b,Gad1,Hat1,Zc3h15,Mtch2,Celf1,Psmc3,Ambra1,Spred1,Eif2ak4,Pak6,Chp1,Rtf1,Stk35,Ptpra,Fkbp1a,Csnk2a1,Hck,Asxl1,Chmp4b,Itch,Trp53inp2,Mmp24,Rpn2,Top1,Pkig,Ptpn1,Adrm1,Mindy3,Dnajc1,Abi1,Spopl,Rc3h2,Psmb7,Ppp6c,Galnt3,Atf2,Zdhhc5,Ldlrad3,Trim44,Caprin1,Hipk3,Ehd4,Ubr1,Trpm7,Ciao1,Anapc1,Ubox5,Rnf24,Tasp1,Bcl2l1,Trpc4ap,Edem2,Cpne1,Adnp,Pmepa1,Eef1a2,Ythdf3,Nceh1,Rpl22l1,Usp13,Exosc9,Noct,Naa15,Foxo1,Dclk1,Tiparp,Ppm1l,Ash1l,Pbxip1,Crtc2,Gatad2b,Otud7b,Rnf115,Sec22b,Csde1,Trim33,Camk2d,Ube2d3,Eif4e,Gtf2b,Ddah1,Setd7,Wwtr1,Dhx36,Ccnl1,B3galnt1,Pdcd10,Rapgef2,Fnip2,Lmna,Chtop,Psmd4,Man1a2,Hipk1,Magi3,Lrig2,Cttnbp2nl,Sars,Ostc,Tet2,Metap1,Rap1gds1,Pkn2,Prkacb,Sdcbp,Map3k7,Rngtt,Dnaja1,Nfx1,Ubap1,Dcaf10,Ncbp1,Anp32b,Rad23b,Kdm4c,Acer2,Lepr,Usp24,Magoh,Tut4,Rab3b,Nrd1,Faf1,Pik3r3,Inpp5b,Stk40,Psmb2,Sfpq,Pum1,Ece1,Eif4g3,Ubr4,Mtor,Errfi1,Cdk11b,Ssu72,Dvl1,Ube2j2,Pdp1,B4galt1,Erp44,Elp1,Ecpas,Caap1,Plaa,Mysm1,Jun,Jak1,Zyg11b,Rnf11,Mast2,Plk3,Ybx1,Rlf,Thrap3,Ago3,Rbbp4,Khdrbs1,Rps6ka1,Man1c1,Pithd1,Kdm1a,Cdc42,Prdm2,Tnfrsf1b,Ube4b,Spsb1,Camta1,Psmc2,Kmt2e,Klhl7,Nub1,Galnt11,Dnajb6,Maea,Nsd2,Rnf4,Htt,Ube2k,Uchl1,Tmem165,Rest,Bmp2k,Cops4,Pkd2,Mtf2,Dr1,Tpst2,Pxn,Gcn1,Wsb2,Tesc,Rpl6,Naa25,Brap,Ppp1cc,Pptc7,Rnf34,Tmed2,Eif3b,Wipi2,Lmtk2,Trrap,Uspl1,Brca2,Cyp51,Ptpn12,Kmt2c,Eif2b4,Ppm1g,Fbxl5,Ppargc1a,Tec,Clock,Uba6,Ccni,Cnot6l,Mapk10,Gak,Ep400,Grk3,Sart3,Coro1c,Rnf10,Ptpn11,Vps37b,Rcc1l,Eif4h,Prkrip1,Prkar1b,Rnf216,Rac1,Trim24,Cul1,Gars,Smarcad1,Prdm5,Rnf103,Aup1,Dysf,Aak1,Gfpt1,Setd5,Marchf8,Kdm5a,Lpcat3,Chd4,Ptpro,Stk38l,Ube2h,Cnot4,Hipk2,Kdm7a,Braf,Rmnd5a,Kdm3a,Usp39,Kcmf1,Paip2b,Cnbp,Rab7,Rad18,Camk1,Ret,Rimklb,Dusp16,Kras,Usp29,Rps5,Sympk,Hnrnpl,Akt1s1,Herc2,Otud7a,Selenos,Acan,Pde8a,Efl1,Grm5,Picalm,Nars2,Pak1,Arrb1,Rab6a,Usp47,Spon1,Rbbp6,Tnrc6a,Rnf40,Setd1a,Bag3,Inpp5f,Ptpre,Ppp2r2d,Pwwp2b,Psmd13,Ppp6r1,Sae1,Sptbn4,Psmc4,Samd4b,Gpi1,Man2a2,Furin,Sec11a,Btbd1,Eed,Uvrag,Spcs2,Rnf169,Ppme1,Atg16l2,Rnf121,Nrip3,Rnf141,Eif4g2,Psma1,Smg1,Gprc5b,Dcun1d3,Usp31,Eif3c,Tollip,Mob2,Dusp8,Cars,Kat6a,Nsd3,Mfhas1,Vps37a,Ufsp2,Hpf1,Sh3rf1,Marchf1,Otud4,Anapc10,Lonp2,Rspry1,Aars,Znrf1,Afg3l1,Trim67,Itgb1,Insr,Elavl1,Pcid2,Adam9,Klkb1,Cpe,Gatad2a,Unc13a,Smad1,Abce1,Smarca5,Gab1,Usp38,Siah1a,N4bp1,Brd7,Cnot1,Ist1,Il34,Sf3b3,Glg1,Rnf166,Dcun1d5,Ilf3,Carm1,Smarca4,Prkcsh,Ddx6,Pcsk7,Sik3,Ireb2,Psma4,Ube2q2,Ptpn9,Nptn,Herc1,Arpp19,Senp6,Plod2,Xrn1,Msl2,Dcaf1,Rhoa,Usp4,Celsr3,Setd2,Ctnnb1,Nktr,Snrk,Yap1,Stt3a,Ubash3b,Sorl1,Kmt2a,Sik2,Cul5,Peak1,Arih1,Fem1b,Map2k1,Snx1,Fbxl22,Rnf111,Mapk6,Eef1a1,Syncrip,Morf4l1,Dipk2a,Armc8,Nck1,Mapkapk3,Arih2,Ptpn23,Pdcd6ip,Cnot10,Stt3b,Higd1a,Lats1,Ppil4,Hbs1l,Ptprk,Snx3,Atg5,Ascc3,Nus1,Ranbp2,Jmjd1c,Bcr,Ube2g2,Dot1l,Ube2n,Btg1,Ppp1r12a,Rnf41,Pym1,Sarnp,Tab2,Rnf217,Dse,Ddx21,Prmt2,Cry1,Scyl2,Mdm2,Cand1,Tbk1,Usp15,Tbc1d10a,Ascc2,Xbp1,Ogdh,Ppp3r1,Spred2,Rab1a,Peli1,Usp34,Bcl11a,Ppp4r3b,Rtn4,Psme4,Cpeb4,Fbxw11,Rnf145,Rnf130,Clk4,Ppp2ca,P4ha2,Larp1,Mprip,Map2k3,Per1,Fxr2,Ube2g1,Zzef1,Myo1c,Ywhae,Blmh,Ssh2,Nf1,Suz12,Rhbdl3,Psmd11,Ppm1d,Rnft1,Mmd,Spag9,Spop,Psmb3,Cdk12,Psmd3,Casc3,Eif1,Psme3,Nmt1,Tlk2,Ace,Prkar1a,Rpl38,Sap30bp,Unk,Rptor,Rnf185,Mtmr3,Nf2,Rars,Cyfip2,Cnot6,Sqstm1,Canx,Ube2b,Cops3,Chd3,Eif4a1,Cpd,Taok1,Supt6,Tnfaip1,Nlk,Wsb1,Rffl,Ggnbp2,Usp32,Appbp2,Rps6kb1,Ppm1e,Scpep1,Kat7,Npepps,Med1,Dusp3,Hdac5,Kansl1,Cdc27,Ccdc47,Ern1,Pecam1,Smurf2,Prkca,Ube2o,Usp36,Nploc4,P4hb,Csnk1d,Wdr45b,Pum2,Rock2,Odc1,Eipr1,Alkal2,Brms1l,Psma3,Ppm1a,Mnat1,Psen1,Psmc1,Bdkrb2,Gskip,Ccnk,ENSMUSG00000097451,Mirg,Ppp2r5

In [70]:
gost_results$result = gost_results$result %>%
    filter(term_size < 500) %>%
    rowwise %>%
    mutate(gene_ids = str_split(intersection, fixed(','))) %>%
    mutate(gene_ids = {hubgenes %>% 
                       filter(name %in% query) %>%
                       filter(gene %in% gene_ids) %>% 
                       pull(gene) %>% 
                       paste0(collapse=',')}) %>%
    ungroup


In [72]:
gost_results$result %>% pull(intersection) %>% head

[1] "Dnajb2,Psmd1,Ubxn4,Edem3,Cop1,Ube2w,Sumo1,Cul3,Trip12,Wdr26,Psmd14,Ubr3,Psmc3,Itch,Spopl,Ubr1,Anapc1,Trpc4ap,Edem2,Ube2d3,Wwtr1,Psmd4,Sdcbp,Rad23b,Faf1,Dvl1,Ube2j2,Ecpas,Plaa,Zyg11b,Plk3,Ube4b,Spsb1,Psmc2,Nub1,Maea,Rnf4,Ube2k,Rnf34,Fbxl5,Clock,Rnf216,Cul1,Rnf103,Aup1,Ube2h,Rmnd5a,Herc2,Selenos,Arrb1,Psmc4,Rnf121,Anapc10,Znrf1,Siah1a,N4bp1,Ctnnb1,Arih1,Fem1b,Fbxl22,Armc8,Arih2,Stt3b,Ascc3,Ube2g2,Rnf217,Mdm2,Ascc2,Peli1,Fbxw11,Ube2g1,Spop,Psmb3,Tlk2,Rnf185,Canx,Ube2b,Tnfaip1,Rffl,Appbp2,Cdc27,Ccdc47,Smurf2,Nploc4,Csnk1d,Psen1,Psmc1,Ppp2r5c,Ubxn2a,Hectd1,Fbxo33,Nemf,Trim9,Rnf144b,Faf2,Fbxl21,Sgtb,Ercc8,Plk2,Ubqln1,Psmc6,Siah3,Mapk8,Pcbp2,Fbxo4,Marchf6,Rnf19a,Eif3h,Clec16a,Psmd2,Gsk3b,Usp7,Ube2v2,Pcnp,Axin1,Trim39,Cd2ap,Ubr2,Cul2,Wac,Csnk1a1,Usp14,Fem1c,Ddb1,Btrc,Otud5,Usp9x,Araf,Huwe1,Cul4b"                           
[2] "Elk4,Kdm5b,Zfp451,Kansl3,Bard1,Trip12,Hdac4,Cdc73,Rnf2,Epc2,Hat1,Rtf1,Asxl1,Atf2,Ash1l,Pbxip1,Crtc2,Gatad2b,Gtf2b,Setd7,Lmna,Chtop,Tet2,Map3k7,Kdm4c,Sfpq,Mysm1,Rlf,Rbbp4,Kdm1a,Prdm2,Kmt2e,Nsd2,Rest,Mtf2,Dr1,Trrap,Brca2,Kmt2c,Clock,Ep400,Sart3,Smarcad1,Prdm5,Setd5,Kdm5a,Chd4,Kdm7a,Kdm3a,Arrb1,Rnf40,Setd1a,Pwwp2b,Eed,Kat6a,Nsd3,Hpf1,Gatad2a,Smarca5,Brd7,Sf3b3,Carm1,Smarca4,Msl2,Setd2,Ctnnb1,Kmt2a,Morf4l1,Atg5,Jmjd1c,Dot1l,Ube2n,Ddx21,Prmt2,Usp15,Xbp1,Per1,Myo1c,Suz12,Sap30bp,Ube2b,Chd3,Supt6,Kat7,Hdac5,Kansl1,Usp36,Brms1l,ENSMUSG00000097451,Mirg,Rcor1,Arid4b,Jarid2,Phf2,Isl1,Atxn7,Bap1,Parg,Ercc6,Mapk8,Phf20l1,Ep300,Nipbl,Ubr5,Taf2,Brd1,Usp16,Crebbp,Glyr1,Paxbp1,Brd4,Vegfa,Ubr2,Wac,Iws1,Mbd2,Epc1,Hdac3,Smad4,Kmt5b,Brms1,Ddb1,Pcgf5,Kdm2a,Oga,Kdm6a,Brcc3,Taf1,Phf8,Huwe1,Kdm5c,Usp51,Rbbp7,Cul4b,Mecp2,Hdac8,Atrx,Morf4l2"
[3] "Gigyf2,Mapkapk2,Btg2,Cdc73,Dhx9,Hnrnpu,Celf1,Rc3h2,Ubox5,Rbm39,Ythdf3,Exosc9,Noct,Celf3,Csde1,Dhx36,Ahcyl1,Virma,Ncbp1,Magoh,Tut4,Pum1,Srsf4,Srsf10,Mtor,Ptbp3,Ybx1,Thrap3,Ago3,Khdrbs1,Rest,Ythdc1,Srsf9,Sfswap,Cnot6l,Srrm4,Hnrnpa2b1,Hnrnpl,Tnrc6a,Rnf40,Fus,Supt5,Samd4b,Snrnp70,Nup98,Elavl1,Pcid2,Cnot1,Celf6,Tent5a,Syncrip,Rbm5,Cpsf6,Larp1,Alkbh5,Taf15,Casc3,Cnot6,Nsrp1,Supt6,Pum2,Rbm25,Zc3h14,Papola,Larp4b,Paip1,Hnrnpk,Samd4,Mbnl2,Hnrnpc,Hsf1,Csdc2,Pabpc1,Ago2,Zc3h3,Puf60,Rbfox2,Ccnt1,Son,Dyrk1a,Tra2b,Srsf3,Srpk1,Hnrnpm,Vegfa,Srsf7,Iws1,Rock1,Celf4,Sf1,Srpk3"                                                                                                                                                                                                                                                                      
[4] "Klhl12,Stx6,Vamp4,Copa,Cul3,Blzf1,Sec23b,Tbc1d20,Arfgef2,Sec16a,Rab14,Sec22b,Sort1,Sec24d,Cog6,Nbea,Sec24b,Eps15,Htt,Stx18,Uso1,Pitpnb,Tmed2,Kdelr2,Chic2,Sec31a,Gak,Cux1,Golt1b,Ccdc91,Creb3l2,Rbsn,Ergic2,Whamm,Rab6a,Uvrag,Copb1,Ap1g1,Cog4,Zw10,Dop1a,Rab6b,Golga4,Sorl1,Arcn1,Snx1,Dipk2a,Sar1a,Ank3,Gopc,Trappc10,Mon2,Ykt6,Rab1a,Vps54,Sar1b,Vamp2,Rabep1,Rab34,Sec24a,Arf1,Gosr1,Gosr2,Scfd1,Rab10,Sec23a,Tmed10,Trip11,Trappc13,Sec24c,Arf4,Exoc5,Cog3,Golph3,Trappc9,Arfgap3,Arf3,Vapa,Rab31,Prepl,Ap3s1,Yipf5,Spire1,Stx5a,Gbf1"                                                                                                                                                                                                                                                                                                               
[5] "Creb1,Agfg1,Klhl12,Stx6,Vamp4,Als2,Ptprn,Cul3,Dnm3,Stam,Chp1,Snap25,Sec23b,Tbc1d20,Chmp4b,Arfgef2,Rab22a,Sec16a,Stxbp1,Rab14,Sec22b,Sort1,Sec24d,Syt11,Gnai3,Sec24b,Sdcbp,Hook1,Stx12,Uso1,Sec31a,Coro1c,Dysf,Arl8b,Wasl,Rab7,Tmcc1,Picalm,Stx4a,Nectin2,Uvrag,Stx1b,Ap1g1,Hook3,Clcn3,Unc13a,Rab27a,Pdcd6ip,Snx3,Sar1a,Trappc10,Ap1b1,Rab1a,Sar1b,Vamp2,Rab34,Sqstm1,Sec24a,Arf1,Pafah1b1,Gosr1,Snx11,Pip4k2b,Rab5c,Plekhm1,Gosr2,Sec23a,Trim9,Tmed10,Trappc13,Sec24c,Ap3m1,Golph3,Laptm4b,Trappc9,Arfgap3,Vps8,Synj1,Rab5a,Cd2ap,Vapa,Ap3s1,Kif5b,Yipf5,Stx5a,Osbp,Pi4k2a,Gbf1"                                                                                                          

In [41]:
hubgenes %>% filter(name == 'kME1') %>% arrange(desc(value))

gene               name value      
1    Cpe                kME1 0.9125162  
2    Marchf11           kME1 0.9034270  
3    Asap1              kME1 0.9033861  
4    Rad54l2            kME1 0.9027221  
5    N4bp2l1            kME1 0.8935717  
6    Ell2               kME1 0.8929045  
7    Lepr               kME1 0.8848906  
8    Ncoa2              kME1 0.8841426  
9    Syndig1            kME1 0.8793334  
10   Fndc3a             kME1 0.8790273  
11   Sv2c               kME1 0.8692756  
12   Chd7               kME1 0.8650474  
13   Vcl                kME1 0.8639747  
14   Slc35f3            kME1 0.8579312  
15   Oxr1               kME1 0.8573361  
16   Pde10a             kME1 0.8565666  
17   Trim9              kME1 0.8536347  
18   Atxn10             kME1 0.8509004  
19   ENSMUSG00000092090 kME1 0.8469017  
20   ENSMUSG00000118257 kME1 0.8364634  
21   Zwint              kME1 0.8353192  
22   Pak3               kME1 0.8320884  
23   Phf8               kME1 0.8304654  
24   Rab3b              kME1 0.8249294  
25   Psme4              kME1 0.8249001  
26   Bbx                kME1 0.8211358  
27   Ptprn              kME1 0.8209191  
28   Prkca              kME1 0.8169769  
29   Cop1               kME1 0.8164328  
30   Wdfy1              kME1 0.8153882  
⋮    ⋮                  ⋮    ⋮          
2442 Ank3               kME1 0.117825092
2443 Kcnk9              kME1 0.116277101
2444 Suz12              kME1 0.114674028
2445 Grk3               kME1 0.113813139
2446 Epb41l5            kME1 0.112522726
2447 Rab28              kME1 0.112500657
2448 Xpo7               kME1 0.111572605
2449 Itm2b              kME1 0.111559331
2450 Maml3              kME1 0.111175301
2451 Atrx               kME1 0.109445734
2452 Frem1              kME1 0.109361292
2453 ENSMUSG00000112558 kME1 0.108634403
2454 Gpc6               kME1 0.103845058
2455 Spire1             kME1 0.097144208
2456 ENSMUSG00000097971 kME1 0.096604946
2457 Srsf7              kME1 0.094951892
2458 Rock1              kME1 0.094759919
2459 Rev1               kME1 0.092486789
2460 Zdbf2              kME1 0.091872705
2461 Ncam2              kME1 0.091439955
2462 Nptn               kME1 0.071049064
2463 Bmpr1a             kME1 0.067715409
2464 4930598N05Rik      kME1 0.065727193
2465 Snrnp70            kME1 0.065248095
2466 Marchf1            kME1 0.064908194
2467 Ankrd12            kME1 0.060985289
2468 Luc7l3             kME1 0.054504218
2469 ENSMUSG00000101621 kME1 0.049346893
2470 Ptpn4              kME1 0.031337263
2471 Il1rap             kME1 0.009925054

In [42]:
gost_results$result %>% 
select(query, query_size) %>%
distinct

query    query_size
1  Agrp_M01 2340      
2  Agrp_M01 2332      
3  Agrp_M01 2336      
4  Agrp_M01  661      
5  Agrp_M01 1077      
6  Agrp_M01 1386      
7  Agrp_M01 1216      
8  Agrp_M01 2383      
9  Agrp_M01  679      
10 Agrp_M02  228      
11 Agrp_M02  229      
12 Agrp_M02  232      
13 Agrp_M02   65      
14 Agrp_M02   93      
15 Agrp_M02  135      
16 Agrp_M03   34      
17 Agrp_M04   84      
18 Agrp_M04   87      
19 Agrp_M04   85      
20 Agrp_M04   28      
21 Agrp_M04   23      
22 Agrp_M05   72      
23 Agrp_M05   73      
24 Agrp_M05   33      
25 Agrp_M06    5      
26 Agrp_M06   72      
27 Agrp_M06   74      
28 Agrp_M06   27      
29 Agrp_M06   25      
30 Agrp_M07    4      
31 Agrp_M07   66      
32 Agrp_M07   63      
33 Agrp_M07   62      
34 Agrp_M07   25      
35 Agrp_M07   44      
36 Agrp_M07   16      
37 Agrp_M08   52      
38 Agrp_M08   50      
39 Agrp_M08   18      
40 Agrp_M08   33      
41 Agrp_M08   31      
42 Agrp_M08   53      
43 Agrp_M08   17      
44 Agrp_M09   53      
45 Agrp_M09   16      
46 Agrp_M09   26      
47 Agrp_M10   48      
48 Agrp_M10   50

In [54]:
result = gost_results$result
result = result %>% mutate(module = query, .keep='unused') %>% relocate(module)

In [104]:
combine_gost_outputs = function(gost_results, top_table, max_term_size=500){
    result = gost_results$result = gost_results$result %>%
        filter(term_size <= max_term_size) %>%
        rename(module = query)
    #join
    result = left_join(x=top_table, y=result, by = 'module')
    #make it smaller
    drop_cols = c("AveExpr", "t", "P.Value", "B", "precision", "recall", "source_order", "parents", "evidence_codes", "effective_domain_size")
    result = result %>%
    select(-any_of(drop_cols)) %>%
    select(-significant.y) %>% #gprofiler returns only significant
    rename(lm_logFC = logFC) %>%
    rename(lm_padj = adj.P.Val) %>%
    rename(lm_significant = significant.x) %>%
    rename(gp_padj = p_value) %>%
    relocate(term_id, .after=gp_padj) %>%
    relocate(term_name, .after=term_id)
    result
}

In [105]:
drop_cols = c("AveExpr", "t", "P.Value", "B", "precision", "recall", "source_order", "parents", "evidence_codes")
result %>%
select(-any_of(drop_cols)) %>% colnames

[1] "comparison"            "module"                "lm_logFC"             
 [4] "lm_padj"               "lm_significant"        "gp_padj"              
 [7] "term_size"             "query_size"            "intersection_size"    
[10] "term_id"               "term_name"             "source"               
[13] "effective_domain_size" "intersection"          "gene_ids"

In [106]:
gost_results = qs::qread('_targets/objects/gost_result_Agrp')
top_table = qs::qread('_targets/objects/top_table_Agrp')
result = combine_gost_outputs(gost_results, top_table)
result %>% head

comparison            module   lm_logFC     lm_padj      lm_significant
1 Day5.obob.FGF1vsVehPF Agrp_M01 -0.006819542 2.208316e-07 TRUE          
2 Day5.obob.FGF1vsVehPF Agrp_M01 -0.006819542 2.208316e-07 TRUE          
3 Day5.obob.FGF1vsVehPF Agrp_M01 -0.006819542 2.208316e-07 TRUE          
4 Day5.obob.FGF1vsVehPF Agrp_M01 -0.006819542 2.208316e-07 TRUE          
5 Day5.obob.FGF1vsVehPF Agrp_M01 -0.006819542 2.208316e-07 TRUE          
6 Day5.obob.FGF1vsVehPF Agrp_M01 -0.006819542 2.208316e-07 TRUE          
  gp_padj      term_id   
1 9.269336e-36 GO:0043161
2 3.642879e-35 GO:0016570
3 2.343913e-23 GO:1903311
4 4.621976e-23 GO:0048193
5 9.657872e-21 GO:0016050
6 2.159760e-18 GO:0007030
  term_name                                                         term_size
1 proteasome-mediated ubiquitin-dependent protein catabolic process 428      
2 histone modification                                              480      
3 regulation of mRNA metabolic process                              308      
4 Golgi vesicle transport                                           276      
5 vesicle organization                                              314      
6 Golgi organization                                                139      
  query_size intersection_size source effective_domain_size
1 2340       130               GO:BP  27350                
2 2340       138               GO:BP  27350                
3 2340        91               GO:BP  27350                
4 2340        85               GO:BP  27350                
5 2340        88               GO:BP  27350                
6 2340        53               GO:BP  27350                
  intersection                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
1 Dnajb2,Psmd1,Ubxn4,Edem3,Cop1,Ube2w,Sumo1,Cul3,Trip12,Wdr26,Psmd14,Ubr3,Psmc3,Itch,Spopl,Ubr1,Anapc1,Trpc4ap,Edem2,Ube2d3,Wwtr1,Psmd4,Sdcbp,Rad23b,Faf1,Dvl1,Ube2j2,Ecpas,Plaa,Zyg11b,Plk3,Ube4b,Spsb1,Psmc2,Nub1,Maea,Rnf4,Ube2k,Rnf34,Fbxl5,Clock,Rnf216,Cul1,Rnf103,Aup1,Ube2h,Rmnd5a,Herc2,Selenos,Arrb1,Psmc4,Rnf121,Anapc10,Znrf1,Siah1a,N4bp1,Ctnnb1,Arih1,Fem1b,Fbxl22,Armc8,Arih2,Stt3b,Ascc3,Ube2g2,Rnf217,Mdm2,Ascc2,Peli1,Fbxw11,Ube2g1,Spop,Psmb3,Tlk2,Rnf185,Canx,Ube2b,Tnfaip1,Rffl,Appbp2,Cdc27,Ccdc47,Smurf2,Nploc4,Csnk1d,Psen1,Psmc1,Ppp2r5c,Ubxn2a,Hectd1,Fbxo33,Nemf,Trim9,Rnf144b,Faf2,Fbxl21,Sgtb,Ercc8,Plk2,Ubqln1,Psmc6,Siah3,Mapk8,Pcbp2,Fbxo4,Marchf6,Rnf19a,Eif3h,Clec16a,Psmd2,Gsk3b,Usp7,Ube2v2,Pcnp,Axin1,Trim39,Cd2ap,Ubr2,Cul2,Wac,Csnk1a1,Usp14,Fem1c,Ddb1,Btrc,Otud5,Usp9x,Araf,Huwe1,Cul4b                           
2 Elk4,Kdm5b,Zfp451,Kansl3,Bard1,Trip12,Hdac4,Cdc73,Rnf2,Epc2,Hat1,Rtf1,Asxl1,Atf2,Ash1l,Pbxip1,Crtc2,Gatad2b,Gtf2b,Setd7,Lmna,Chtop,Tet2,Map3k7,Kdm4c,Sfpq,Mysm1,Rlf,Rbbp4,Kdm1a,Prdm2,Kmt2e,Nsd2,Rest,Mtf2,Dr1,Trrap,Brca2,Kmt2c,Clock,Ep400,Sart3,Smarcad1,Prdm5,Setd5,Kdm5a,Chd4,Kdm7a,Kdm3a,Arrb1,Rnf40,Setd1a,Pwwp2b,Eed,Kat6a,Nsd3,Hpf1,Gatad2a,Smarca5,Brd7,Sf3b3,Carm1,Smarca4,Msl2,Setd2,Ctnnb1,Kmt2a,Morf4l1,Atg5,Jmjd1c,Dot1l,Ube2n,Ddx21,Prmt2,Usp15,Xbp1,Per1,Myo1c,Suz12,Sap30bp,Ube2b,Chd3,Supt6,Kat7,Hdac5,Kansl1,Usp36,Brms1l,ENSMUSG00000097451,Mirg,Rcor1,Arid4b,Jarid2,Phf2,Isl1,Atxn7,Bap1,Parg,Ercc6,Mapk8,Phf20l1,Ep300,Nipbl,Ubr5,Taf2,Brd1,Usp16,Crebbp,Glyr1,Paxbp1,Brd4,Vegf

In [96]:
    result = gost_results$result = gost_results$result %>%
        filter(term_size <= 500) %>%
        rename(module = query)
result %>% head

ERROR: [1m[33mError[39m in [1m[1m`chr_as_locations()`:[22m
[33m![39m Can't rename columns that don't exist.
[31m✖[39m Column `query` doesn't exist.


In [63]:
result %>% colnames

[1] "comparison"            "module"                "logFC"                
 [4] "AveExpr"               "t"                     "P.Value"              
 [7] "adj.P.Val"             "B"                     "significant.x"        
[10] "significant.y"         "p_value"               "term_size"            
[13] "query_size"            "intersection_size"     "precision"            
[16] "recall"                "term_id"               "source"               
[19] "term_name"             "effective_domain_size" "source_order"         
[22] "parents"               "evidence_codes"        "intersection"         
[25] "gene_ids"

In [65]:
result %>% pull(gene_ids) %>% head

[1] "" "" "" "" "" ""

In [115]:
qs::qread('_targets/objects/combined_gost_summary_NFOL') %>% filter(lm_significant == TRUE) %>% filter(comparison == 'Day5.obob.FGF1vsVehPF')

comparison            module   lm_logFC    lm_padj      lm_significant
1   Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
2   Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
3   Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
4   Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
5   Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
6   Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
7   Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
8   Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
9   Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
10  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
11  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
12  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
13  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
14  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
15  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
16  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
17  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
18  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
19  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
20  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
21  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
22  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
23  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
24  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
25  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
26  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
27  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
28  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
29  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
30  Day5.obob.FGF1vsVehPF NFOL_M03 -0.06285952 1.391619e-08 TRUE          
⋮   ⋮                     ⋮        ⋮           ⋮            ⋮             
394 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
395 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
396 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
397 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
398 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
399 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
400 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
401 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
402 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
403 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
404 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
405 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
406 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
407 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
408 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
409 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
410 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
411 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
412 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
413 Day5.obob.FGF1vsVehPF NFOL_M06 -0.03442521 0.001670114  TRUE          
414 Day5.obob.FGF1vsVehPF NFOL_M15  0.02299038 0.043485975  TRUE          
415 Day5.obob.FGF1vsVehPF NFO

In [117]:
targets::tar_meta(fields = error, complete_only = TRUE) %>% filter(str_detect(name, 'combined_gost_summary_')) %>% pull(error) %>% unique

[1] "no applicable method for filter applied to an object of class NULL"   
[2] "no applicable method for left_join applied to an object of class NULL"

In [118]:
qs::qread('../01_milo/combination_recipe.qs')

output_name                              output_suffix        day  
1  combined_da_results_all.BL6d5d14         all.BL6d5d14         all  
2  combined_da_results_all.obob14v14        all.obob14v14        all  
3  combined_da_results_all.obob14vBL6       all.obob14vBL6       all  
4  combined_da_results_all.obob5v5          all.obob5v5          all  
5  combined_da_results_all.obob5vBL6        all.obob5vBL6        all  
6  combined_da_results_all.obobBL6          all.obobBL6          all  
7  combined_da_results_all.obobBL6d14       all.obobBL6d14       all  
8  combined_da_results_all.obobBL6d5        all.obobBL6d5        all  
9  combined_da_results_all.obobFGF1BL6d14   all.obobFGF1BL6d14   all  
10 combined_da_results_all.obobFGF1BL6d5    all.obobFGF1BL6d5    all  
11 combined_da_results_all.obobVeh_PFd5d14  all.obobVeh_PFd5d14  all  
12 combined_da_results_Day14.obob14v14      Day14.obob14v14      Day14
13 combined_da_results_Day14.obobBL6d14     Day14.obobBL6d14     Day14
14 combined_da_results_Day14.obobFGF1BL6d14 Day14.obobFGF1BL6d14 Day14
15 combined_da_results_Day5.obob5v5         Day5.obob5v5         Day5 
16 combined_da_results_Day5.obobBL6d5       Day5.obobBL6d5       Day5 
17 combined_da_results_Day5.obobFGF1BL6d5   Day5.obobFGF1BL6d5   Day5 
   contrast_name  
1  BL6d5d14       
2  obob14v14      
3  obob14vBL6     
4  obob5v5        
5  obob5vBL6      
6  obobBL6        
7  obobBL6d14     
8  obobBL6d5      
9  obobFGF1BL6d14 
10 obobFGF1BL6d5  
11 obobVeh_PFd5d14
12 obob14v14      
13 obobBL6d14     
14 obobFGF1BL6d14 
15 obob5v5        
16 obobBL6d5      
17 obobFGF1BL6d5  
   da_names                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    